# How to customize a CasysPlot

CasysPlot objects and their elements (stat_bar, hist_bar, color_bar, stat_graph, ...) can be customized through various methods and parameters.
This notebook will show some examples.

In [ ]:
import os

os.environ["GES_TABLE_DIR"] = "/data/cvl_exj3/TABLES/DSC"

In [ ]:
from casys import (
    AxeParams,
    CasysPlot,
    DateHandler,
    Field,
    NadirData,
    PlotParams,
    TextParams,
)

NadirData.enable_loginfo()

In [ ]:
start = DateHandler.from_orf("C_J3_GDRD", 122, 1, pos="first")
end = DateHandler.from_orf("C_J3_GDRD", 122, 154, pos="last")

In [ ]:
ad = NadirData(
    date_start=start,
    date_end=end,
    source="TABLE_C_J3_B_GDRD",
    orf="C_J3_GDRD",
    time="time",
    longitude="LONGITUDE",
    latitude="LATITUDE",
)

var_swh = Field(name="swh", source="IIF(FLAG_VAL.ALTI==0, SWH.ALTI,DV)", unit="m")
var_sla = Field(
    name="SLA",
    source="ORBIT.ALTI - RANGE.ALTI - MEAN_SEA_SURFACE.MODEL.CNESCLS15",
    unit="m",
)
var_wtc_rad = Field(
    name="WTC_rad",
    source="IIF(FLAG_VAL.ALTI==0, WET_TROPOSPHERIC_CORRECTION.RAD,DV)",
    unit="m",
)
var_wtc_mod = Field(
    name="WTC_model",
    source="IIF(FLAG_VAL.ALTI==0, WET_TROPOSPHERIC_CORRECTION.MODEL.ECMWF_GAUSS,DV)",
    unit="m",
)
var_range_std_ku = Field(
    name="range_std_ku", source="IIF(FLAG_VAL.ALTI==0, RANGE_STD.ALTI,DV)", unit="m"
)

ad.add_raw_data(name="SLA", field=var_sla)

ad.add_time_stat(name="SLA day", freq="day", field=var_sla, stats=["mean", "count"])
ad.add_time_stat(name="Rad WTC pass", freq="pass", field=var_wtc_rad, stats=["mean"])
ad.add_time_stat(name="Model WTC pass", freq="pass", field=var_wtc_mod, stats=["mean"])
ad.add_time_stat(name="SWH mean by pass", freq="pass", field=var_swh)
ad.add_time_stat(name="SWH mean by day", freq="day", field=var_swh)

ad.add_binned_stat(
    name="Ku-band range std fct swh",
    field=var_range_std_ku,
    x=var_swh,
    res_x=(0, 8, 0.05),
    stats=["mean"],
)

ad.add_geobox_stat(
    name="SLA box stat",
    field=var_sla,
    stats=["count", "median", "std"],
    res_lon=(-180, 180, 2),
    res_lat=(-90, 90, 2),
)

ad.add_crossover_stat(
    name="Crossover SLA",
    field=var_sla,
    max_time_difference="5 days",
    stats=["mean", "count"],
    temporal_stats_freq=["cycle", "day"],
)

ad.compute()

# How to customize text elements on a plot

TexParams is an object allowing to customize text elements of plots.

* [TextParams documentation](../parameters/text_params.rst)

**TextParams** parameters can be strings, or dictionaries:

In [ ]:
text = TextParams(xlabel="the time", ylabel="the SLA", title="a title")

In [ ]:
sladay_mean_plot = CasysPlot(
    data=ad, data_name="SLA day", stat="mean", text_params=text
)

sladay_mean_plot.show()

A single TextParams instance can be used to set multiple plots if you do not include titles in them

In [ ]:
text = TextParams(
    xlabel={"color": "g", "style": "italic"},
    ylabel={"color": "g", "style": "italic"},
    title={"size": "x-large", "weight": "bold"},
)

In [ ]:
sladay_mean_plot.set_text_params(text)

sladay_mean_plot.show()

In [ ]:
sla_cross_mean_plot = CasysPlot(data=ad, data_name="Crossover SLA", stat="mean")
sla_cross_mean_plot.show()
sla_cross_mean_plot.set_text_params(text)
sla_cross_mean_plot.show()

In [ ]:
text = TextParams(
    xlabel={"xlabel": "Time", "color": "g", "style": "italic"},
    ylabel={"ylabel": "Sea level anomaly (meters)", "color": "g", "style": "italic"},
    title={
        "t": "Daily averaged mean of SLA at crossovers",
        "size": "x-large",
        "weight": "bold",
    },
)

In [ ]:
sla_cross_mean_plot = CasysPlot(
    data=ad, data_name="Crossover SLA", freq="day", stat="mean", text_params=text
)

sla_cross_mean_plot.show()

# How to customize axes, color bar or stat bar

**AxeParams** is an object allowing to customize ticks axes, color bar, stat bar...

* [AxeParams documentation](../parameters/axe_params.rst)

## Map plot configuration

This is a plot with very basic PlotParams, but no AxeParams defined:

In [ ]:
slabox_stat = CasysPlot(
    data=ad,
    data_name="SLA box stat",
    stat="std",
    plot_params=PlotParams(color_limits=(0, 1)),
)

slabox_stat.show()

### Configuring the color bar

To configure the default the color bar parameters, we need to define an AxeParams:

In [ ]:
cb_params = AxeParams(
    label="SLA (m)",
    values={
        "ticks": [0.3, 0.45, 0.8],
        "labels": ["low value", "medium value", "high value"],
    },
    position="top",
)

And set it to the *color_bar* property of the PlotParams:

In [ ]:
plot_par = PlotParams(
    color_limits=(0, 1),
    grid=True,
    fill_ocean=False,
    mask_land=True,
    color_bar=cb_params,
)

slabox_stat.set_plot_params(plot_par)
slabox_stat.show()

Another way of configuring the color bar is to use the ``add_color_bar()`` method:

In [ ]:
cb_params = AxeParams(
    label={"label": "custom color bar", "size": "small", "color": "b"},
    ticks={
        "labelsize": "small",
        "labelcolor": "r",
        "width": 2,
        "size": 8,
        "color": "g",
    },
)

In [ ]:
slabox_stat.add_color_bar(
    position="left",
    params=cb_params,
)

slabox_stat.show()

Minor and major ticks are also customizable separately:

In [ ]:
cb_params = AxeParams(
    label={"label": "custom color bar", "size": "small", "color": "b"},
    ticks={
        "labelsize": "small",
        "labelcolor": "r",
        "width": 2,
        "size": 8,
        "color": "g",
    },
    ticks_major={"labelcolor": "b"},
)

In [ ]:
slabox_stat.add_color_bar(
    position="left",
    params=cb_params,
)

slabox_stat.show()

General ticks parameters are applied first then minor and major ticks.

### Customizing the statistics bar

To add the customized statistics bar, we need to define an AxeParams:

In [ ]:
sb_params = AxeParams(label={"fontsize": "small", "weight": "light"}, position="bottom")

And set it to the [add_stat_bar](../generated/casys.visualization.rst#casys.visualization.CasysPlot.add_color_bar) method:

In [ ]:
slabox_stat.add_stat_bar(params=sb_params, position="bottom")

slabox_stat.show()

## Graphic plot configuration

Here is an example of customizing a graph that is a merging of several plots:

Creation of the 3 plots:

In [ ]:
wtcrad_pass_plot = CasysPlot(
    data=ad,
    data_name="Rad WTC pass",
    stat="mean",
    plot_params=PlotParams(
        y_limits=(-0.25, 0.25), line_style="-", marker_style=".", marker_size=6
    ),
)

wtcmod_pass_plot = CasysPlot(data=ad, data_name="Model WTC pass", stat="mean")

rangestd_fctSWH_plot = CasysPlot(
    data=ad, data_name="Ku-band range std fct swh", stat="mean"
)

Add a stat bar to "wtcmod_pass_plot" and merge it with "wtcrad_pass_plot", sharing all axes

In [ ]:
wtcmod_pass_plot.add_stat_bar()
wtcrad_pass_plot.add_plot(wtcmod_pass_plot, shared_ax="all")

Add a stat bar to "rangestd_fctSWH_plot" and merge it with "wtcrad_pass_plot", sharing only the y axe

In [ ]:
rangestd_fctSWH_plot.add_stat_bar()
wtcrad_pass_plot.add_plot(rangestd_fctSWH_plot, shared_ax="y")

Display...

In [ ]:
wtcrad_pass_plot.show()

### Customizing the statistics bar

In [ ]:
wtcrad_pass_plot.add_stat_bar(
    params=AxeParams(label={"style": "italic", "size": "small"})
)

wtcrad_pass_plot.show()

### Setting altimetric ticks with AxeParams

In [ ]:
wtcrad_pass_plot = CasysPlot(
    data=ad,
    data_name="Rad WTC pass",
    stat="mean",
    plot_params=PlotParams(
        y_limits=(-0.25, 0.25), line_style="-", marker_style=".", marker_size=6
    ),
)

wtcrad_pass_plot.show()

#### Pass altimetric ticks on bottom axe

In [ ]:
wtcrad_pass_plot.set_ticks(
    position="bottom",
    fmt="P",
    params=AxeParams(
        label={"label": "Label pass number", "color": "b"},
        ticks={"color": "b", "labelrotation": 40, "width": 5, "labelcolor": "b"},
    ),
)

wtcrad_pass_plot.show()

In [ ]:
wtcrad_pass_plot.add_ticks_space(space=0.05, position="bottom")
wtcrad_pass_plot.show()

#### Cycle altimetric ticks on top axe

In [ ]:
wtcrad_pass_plot.set_ticks(
    position="top",
    fmt="C",
    params=AxeParams(
        label={"label": "Label cycle number", "color": "r"},
        ticks={"color": "r", "labelrotation": 40, "width": 5, "labelcolor": "r"},
    ),
)

wtcrad_pass_plot.show()

### Setting customized ticks with AxeParams

In [ ]:
def custom_tick(value):
    return f"{float(value)+10}%"


wtcrad_pass_plot.set_ticks(
    params=AxeParams(
        position="left",
        label={"label": "Custom axe", "color": "c"},
        ticks={"color": "c", "labelrotation": 40, "width": 5, "labelcolor": "c"},
        values=custom_tick,
    ),
)

wtcrad_pass_plot.show()

In [ ]:
wtcrad_pass_plot.set_ticks(
    position="left",
    params=AxeParams(
        values={"ticks": [-0.15, 0, 0.15], "labels": ["bad", "normal", "good"]}
    ),
)

wtcrad_pass_plot.show()

# How to configure elements sizes

**set_text_size** changes the size of the elements of the plot according to the provided parameters.

* [set_text_size documentation](../cp_main.rst#textual-elements-size)

In [ ]:
wtcrad_pass_plot = CasysPlot(
    data=ad,
    data_name="Rad WTC pass",
    stat="mean",
    plot_params=PlotParams(
        y_limits=(-0.25, 0.25), line_style="-", marker_style=".", marker_size=6
    ),
)

wtcmod_pass_plot = CasysPlot(data=ad, data_name="Model WTC pass", stat="mean")

wtcrad_pass_plot.add_plot(wtcmod_pass_plot)
wtcrad_pass_plot.add_stat_bar()

wtcrad_pass_plot.set_text_size(elements="legend", size="large")
wtcrad_pass_plot.show()

In [ ]:
wtcrad_pass_plot.set_text_size(elements="title", size=15)
wtcrad_pass_plot.show()

In [ ]:
wtcrad_pass_plot.set_text_size(
    elements=["legend", "axes_ticks", "axes_labels", "bars_labels"], size="xx-small"
)

wtcrad_pass_plot.show()

In [ ]:
wtcrad_pass_plot.set_text_size(elements=["axes_labels"], size="large")

wtcrad_pass_plot.show()

In [ ]:
slabox_stat.set_text_size(elements="bars_labels", size="large")
slabox_stat.show()

In [ ]:
slabox_stat.set_text_size(elements="bars_ticks", size="xx-small")
slabox_stat.show()

In [ ]:
slabox_stat.set_text_size(elements="all", size="large")
slabox_stat.show()

# How to add watermarks to a plot

**add_watermark** allows to add a watermark (a logo) to a plot. 

* [add_watermark documentation](../elements/watermark.rst)

In [ ]:
pparams = PlotParams(line_style=":", marker_style="+", marker_size=8, grid=True)
file = "../../resources/CLS-Logo.png"

## Size in pixels, and transparency

In [ ]:
plot = CasysPlot(
    data=ad,
    data_name="SWH mean by day",
    stat="mean",
    plot_params=pparams,
)
plot.add_watermark(
    image=file,
    image_size=(400, 300),
    alpha=0.5,
)
plot.show()

## Height in pixels, position and transparency

In [ ]:
plot = CasysPlot(
    data=ad,
    data_name="SWH mean by day",
    stat="mean",
    plot_params=pparams,
)
plot.add_watermark(
    image=file,
    image_size=(None, 120),
    xo=800,
    yo=70,
    alpha=0.5,
)
plot.show()

## A second watermark

In [ ]:
file2 = "../../resources/CNES-Logo.jpg"

In [ ]:
plot.add_watermark(
    image=file2,
    image_size=(None, 140),
    xo=650,
    yo=60,
    alpha=0.5,
)
plot.show()

## Size in pourcentage of the figure's width

In [ ]:
plot = CasysPlot(
    data=ad,
    data_name="SWH mean by day",
    stat="mean",
    plot_params=pparams,
)
plot.add_watermark(
    image=file,
    image_size=50,
    xo=300,
    yo=100,
    alpha=0.5,
)
plot.show()